In [1]:
import os
import pandas as pd
import altair as alt
import numpy as np
from vega_datasets import data
from altair.expr import datum, geoCentroid
import geopandas as gpd

In [2]:
root = '/Users/cynthiaxu/Documents/MIDS/03_2023 Fall/209 Data Visualization/209-ds-salaries-viz-project/'
folder = 'data'

data_path = os.path.join(root, folder)
data_path

'/Users/cynthiaxu/Documents/MIDS/03_2023 Fall/209 Data Visualization/209-ds-salaries-viz-project/data'

In [3]:
data_files = os.listdir(data_path)
data_files = [file for file in data_files if '2021' in file and '.csv' in file]
data_files

['Data Science Salary 2021 to 2023.csv', 'data_cleaned_2021.csv']

In [4]:
sal_df = pd.read_csv(os.path.join(data_path, data_files[0]))
skill_df = pd.read_csv(os.path.join(data_path, data_files[1]))

In [5]:
sal_df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3756       2020               SE              FT   Principal Data Scientist   
3757       2020               SE              FT             Data Scientist   
3758       2020               SE              FT       Data Science Manager   
3759       2020               SE              FT  Machine Learning Engineer   
3760       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  
0     213660             USD         213660               US            L  
1     130760             USD         130760               US            L  
2     100000             USD         100000               NG            L  
3      30000             USD          30000               NG            L  
4     204620             USD         204620               US            L  
...      ...             ...            ...              ...          ...  
3756  130000             EUR         148261               DE            M  
3757   80000             EUR          91237               AT            S  
3758  190200             USD         190200               US            M  
3759   40000             EUR          45618               HR            S  
3760  412000             USD         412000               US            L  

[3761 rows x 9 columns]

In [6]:
geo_file = [file for file in os.listdir(data_path) if 'countries' in file]

geo_df = pd.read_csv(os.path.join(data_path, geo_file[0]))
for i, col in enumerate(geo_df.columns):
    geo_df.iloc[:, i] = geo_df.iloc[:, i].str.replace('"', '')

geo_df['Alpha-2 code'] = geo_df['Alpha-2 code'].apply(lambda x: x.replace(' ', ''))

geo_df['Alpha-2 code'] = geo_df['Alpha-2 code'].astype(str)
geo_df['Latitude (average)'] = geo_df['Latitude (average)'].astype(float)
geo_df['Longitude (average)'] = geo_df['Longitude (average)'].astype(float)
geo_df

Country Alpha-2 code Alpha-3 code Numeric code  \
0          Afghanistan           AF          AFG            4   
1              Albania           AL          ALB            8   
2              Algeria           DZ          DZA           12   
3       American Samoa           AS          ASM           16   
4              Andorra           AD          AND           20   
..                 ...          ...          ...          ...   
251  Wallis and Futuna           WF          WLF          876   
252     Western Sahara           EH          ESH          732   
253              Yemen           YE          YEM          887   
254             Zambia           ZM          ZMB          894   
255           Zimbabwe           ZW          ZWE          716   

     Latitude (average)  Longitude (average)  
0               33.0000                 65.0  
1               41.0000                 20.0  
2               28.0000                  3.0  
3              -14.3333               -170.0  
4               42.5000                  1.6  
..                  ...                  ...  
251            -13.3000               -176.2  
252             24.5000                -13.0  
253             15.0000                 48.0  
254            -15.0000                 30.0  
255            -20.0000                 30.0  

[256 rows x 6 columns]

In [7]:
df = sal_df.merge(geo_df, left_on=['company_location'], right_on=['Alpha-2 code'], how='left')
df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3761       2020               SE              FT   Principal Data Scientist   
3762       2020               SE              FT             Data Scientist   
3763       2020               SE              FT       Data Science Manager   
3764       2020               SE              FT  Machine Learning Engineer   
3765       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  \
0     213660             USD         213660               US            L   
1     130760             USD         130760               US            L   
2     100000             USD         100000               NG            L   
3      30000             USD          30000               NG            L   
4     204620             USD         204620               US            L   
...      ...             ...            ...              ...          ...   
3761  130000             EUR         148261               DE            M   
3762   80000             EUR          91237               AT            S   
3763  190200             USD         190200               US            M   
3764   40000             EUR          45618               HR            S   
3765  412000             USD         412000               US            L   

            Country Alpha-2 code Alpha-3 code Numeric code  \
0     United States           US          USA          840   
1     United States           US          USA          840   
2           Nigeria           NG          NGA          566   
3           Nigeria           NG          NGA          566   
4     United States           US          USA          840   
...             ...          ...          ...          ...   
3761        Germany           DE          DEU          276   
3762        Austria           AT          AUT           40   
3763  United States           US          USA          840   
3764        Croatia           HR          HRV          191   
3765  United States           US          USA          840   

      Latitude (average)  Longitude (average)  
0                38.0000             -97.0000  
1                38.0000             -97.0000  
2                10.0000               8.0000  
3                10.0000               8.0000  
4                38.0000             -97.0000  
...                  ...                  ...  
3761             51.0000               9.0000  
3762             47.3333              13.3333  
3763             38.0000             -97.0000  
3764             45.1667              15.5000  
3765             38.0000             -97.0000  

[3766 rows x 15 columns]

In [8]:
#jitter points
sigma = 4
df['latitude'] = df['Latitude (average)'].apply(lambda x: np.random.normal(x, sigma, 1)).astype(float)
df['longitude'] = df['Longitude (average)'].apply(lambda x: np.random.normal(x, sigma, 1)).astype(float)
df

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT       Data Quality Analyst   
3          2023               EN              FT    Compliance Data Analyst   
4          2023               EN              FT          Applied Scientist   
...         ...              ...             ...                        ...   
3761       2020               SE              FT   Principal Data Scientist   
3762       2020               SE              FT             Data Scientist   
3763       2020               SE              FT       Data Science Manager   
3764       2020               SE              FT  Machine Learning Engineer   
3765       2020               SE              FT             Data Scientist   

      salary salary_currency  salary_in_usd company_location company_size  \
0     213660             USD         213660               US            L   
1     130760             USD         130760               US            L   
2     100000             USD         100000               NG            L   
3      30000             USD          30000               NG            L   
4     204620             USD         204620               US            L   
...      ...             ...            ...              ...          ...   
3761  130000             EUR         148261               DE            M   
3762   80000             EUR          91237               AT            S   
3763  190200             USD         190200               US            M   
3764   40000             EUR          45618               HR            S   
3765  412000             USD         412000               US            L   

            Country Alpha-2 code Alpha-3 code Numeric code  \
0     United States           US          USA          840   
1     United States           US          USA          840   
2           Nigeria           NG          NGA          566   
3           Nigeria           NG          NGA          566   
4     United States           US          USA          840   
...             ...          ...          ...          ...   
3761        Germany           DE          DEU          276   
3762        Austria           AT          AUT           40   
3763  United States           US          USA          840   
3764        Croatia           HR          HRV          191   
3765  United States           US          USA          840   

      Latitude (average)  Longitude (average)   latitude   longitude  
0                38.0000             -97.0000  37.516011  -99.070194  
1                38.0000             -97.0000  40.082642  -92.673900  
2                10.0000               8.0000   6.808547    2.451013  
3                10.0000               8.0000   8.469037    1.260132  
4                38.0000             -97.0000  32.272967  -95.736586  
...                  ...                  ...        ...         ...  
3761             51.0000               9.0000  49.525183    9.809548  
3762             47.3333              13.3333  55.146326   16.714777  
3763             38.0000             -97.0000  44.697727  -94.218246  
3764             45.1667              15.5000  50.689689   15.060592  
3765             38.0000             -97.0000  37.813027 -103.692409  

[3766 rows x 17 columns]

In [9]:
#iteration 1
countries = alt.topo_feature(data.world_110m.url, 'countries')

background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=800,
    height=400
)

points = alt.Chart(df, title = 'Location of Data Science Roles').mark_circle().encode(
    longitude='longitude:Q',
    latitude='latitude:Q',
    size=alt.value(10)
    # tooltip='name'
)

iter1 = background + points
iter1.save(os.path.join(root, 'images', 'iteration1.html'))
iter1

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [10]:
#try with bubbles to represent median salary
med_series = df.groupby(["company_location"])["salary_in_usd"].median()

df_2 = df.merge(med_series, on='company_location')
df_2 = df_2.rename(columns={'salary_in_usd_y': 'median_salary'})
df_2

work_year experience_level employment_type                  job_title  \
0          2023               EN              FT          Applied Scientist   
1          2023               EN              FT          Applied Scientist   
2          2023               EN              FT          Applied Scientist   
3          2023               EN              FT          Applied Scientist   
4          2023               EN              FT  Machine Learning Engineer   
...         ...              ...             ...                        ...   
3761       2021               MI              FT          Big Data Engineer   
3762       2021               MI              FT              Data Engineer   
3763       2021               SE              FT               Data Analyst   
3764       2020               MI              FT       Product Data Analyst   
3765       2020               SE              FT         Lead Data Engineer   

      salary salary_currency  salary_in_usd_x company_location company_size  \
0     213660             USD           213660               US            L   
1     130760             USD           130760               US            L   
2     204620             USD           204620               US            L   
3     110680             USD           110680               US            L   
4     163196             USD           163196               US            M   
...      ...             ...              ...              ...          ...   
3761   18000             USD            18000               MD            S   
3762   24000             EUR            28369               MT            L   
3763   50000             USD            50000               PH            S   
3764   20000             USD            20000               HN            S   
3765  125000             USD           125000               NZ            S   

                   Country Alpha-2 code Alpha-3 code Numeric code  \
0            United States           US          USA          840   
1            United States           US          USA          840   
2            United States           US          USA          840   
3            United States           US          USA          840   
4            United States           US          USA          840   
...                    ...          ...          ...          ...   
3761  Moldova, Republic of           MD          MDA          498   
3762                 Malta           MT          MLT          470   
3763           Philippines           PH          PHL          608   
3764              Honduras           HN          HND          340   
3765           New Zealand           NZ          NZL          554   

      Latitude (average)  Longitude (average)   latitude   longitude  \
0                38.0000             -97.0000  37.516011  -99.070194   
1                38.0000             -97.0000  40.082642  -92.673900   
2                38.0000             -97.0000  32.272967  -95.736586   
3                38.0000             -97.0000  38.861532  -98.736880   
4                38.0000             -97.0000  38.634602  -91.772408   
...                  ...                  ...        ...         ...   
3761             47.0000              29.0000  51.773777   32.471883   
3762             35.8333              14.5833  37.272238   16.315570   
3763             13.0000             122.0000   4.495731  126.557769   
3764             15.0000             -86.5000  17.445177  -84.369822   
3765            -41.0000             174.0000 -44.491798  182.449979   

      median_salary  
0          145000.0  
1          145000.0  
2          145000.0  
3          145000.0  
4          145000.0  
...             ...  
3761        18000.0  
3762        28369.0  
3763        50000.0  
3764        20000.0  
3765       125000.0  

[3766 rows x 18 columns]

In [11]:
#iteration 2
#try with bubbles to represent median salary

background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=800,
    height=400
)

bubbles = alt.Chart(df, title = 'Median Data Science Salaries by Country').transform_calculate(
    centroid=geoCentroid(None, datum)
).mark_circle(
    stroke='navy'
).encode(
    longitude='Longitude (average):Q',
    latitude='Latitude (average):Q',
    color="median_salary:Q",
    size="median_salary:Q"
)

iter2 = background + bubbles
iter2.save(os.path.join(root, 'images', 'iteration2.html'))
iter2

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [12]:
#iteration 3
#try a choropleth
world_map_data = alt.topo_feature('https://vega.github.io/vega-datasets/data/world-110m.json', 'countries')
background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=500,
    height=300
)

choro = alt.Chart(df).mark_geoshape().encode(
    alt.Color('median_salary:Q', scale=alt.Scale(scheme='viridis')),
    tooltip=['Country:N', 'median_salary:Q']
).project(
    "equirectangular"
).properties(
    width=500,
    height=300,
    title='Median Salary by Country'
)

background + choro

/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_name].apply(to_list_if_array, convert_dtype=False)
/Library/Frameworks/Python.framework/Versions/3.11/lib/python3.11/site-packages/altair/utils/core.py:410: FutureWarning: the convert_dtype parameter is deprecated and will be removed in a future version.  Do ``ser.astype(object).apply()`` instead if you want ``convert_dtype=False``.
  col = df[col_n

alt.LayerChart(...)

In [13]:
df.to_csv(os.path.join(root, 'data', 'salary_with_GPS.csv'))

In [15]:
# 1. Load world country boundaries data from an alternative source.
world_url = "https://raw.githubusercontent.com/johan/world.geo.json/master/countries.geo.json"
world = gpd.read_file(world_url)

# Aggregate the df to compute the median salary for each country.
agg_df = df.groupby('Alpha-3 code').agg(median_salary=('salary_in_usd', 'median')).reset_index()

# Rename 'Alpha-3 code' to 'id' in agg_df
agg_df = agg_df.rename(columns={'Alpha-3 code': 'id'})

# Ensure the data types of 'id' columns in both dataframes are the same and strip any spaces
agg_df['id'] = agg_df['id'].astype(str)
agg_df['id'] = agg_df['id'].str.strip()
world['id'] = world['id'].astype(str)

# Merge the aggregated salary data with world country boundaries using a common identifier ('id')
merged_data = pd.merge(agg_df, world, on='id', how='left')

# Drop NaN values for name (or handle them as you see fit)
merged_data = merged_data.dropna(subset=['name'])
# Drop NaN values for median_salary (or handle them as you see fit)
merged_data = merged_data.dropna(subset=['median_salary'])

# Convert the merged_data to GeoDataFrame and then to JSON
gdf = gpd.GeoDataFrame(merged_data, geometry='geometry')
json_data = gdf.to_json()

# 2. Create a choropleth map
choropleth_map = alt.Chart(alt.Data(values=json_data, format=alt.DataFormat(property='features', type='json'))).mark_geoshape().encode(
    color=alt.Color('properties.median_salary:Q', scale=alt.Scale(scheme='viridis'), title='Median Salary',
                    legend=alt.Legend(format=".0f")),
    tooltip=['properties.name:N', 'properties.median_salary:Q']
).project(
    'equirectangular'
).properties(
    width=800,
    height=400,
    title='Median Salary by Country'
)
background = alt.Chart(countries).mark_geoshape(
    fill='lightgray',
    stroke='white'
).project(
    "equirectangular"
).properties(
    width=800,
    height=400
)
iter3 = background + choropleth_map
iter3.save(os.path.join(root, 'images', 'iteration3.html'))
iter3

alt.LayerChart(...)